In [1]:
import pandas as pd
import altair as alt
import warnings

warnings.filterwarnings('ignore', category=FutureWarning)
alt.data_transformers.disable_max_rows()

# Load dataset
url = 'https://github.com/UIUC-iSchool-DataViz/is445_data/raw/main/licenses_fall2022.csv'
df = pd.read_csv(url)

# Convert 'Original Issue Date' to datetime (coerce errors) and drop missing values
df['Original Issue Date'] = pd.to_datetime(df['Original Issue Date'], errors='coerce')
df = df.dropna(subset=['Original Issue Date', 'License Type'])

# Create a Month column (formatted as year-month) for aggregation
df['Month'] = df['Original Issue Date'].dt.to_period('M').astype(str)




In [7]:
#Pie Chart: Distribution of License Types

# Aggregate data to compute counts per license type
license_counts = df['License Type'].value_counts().reset_index()
license_counts.columns = ['License Type', 'Count']

# Create the pie chart (doughnut style by setting innerRadius)
pie_chart = alt.Chart(license_counts).mark_arc(innerRadius=50).encode(
    theta=alt.Theta(field="Count", type="quantitative"),
    color=alt.Color(field="License Type", type="nominal"),
    tooltip=['License Type', 'Count']
).properties(
    title='Distribution of License Types',
    width=300,
    height=300)
pie_chart

alt.Chart(...)

In [11]:
# Composite Bar & Line Chart: Monthly License Issuance

# Create an interactive dropdown parameter for License Type
license_types = df['License Type'].unique().tolist()
license_selector = alt.param(
    name='selectedLicense',
    bind=alt.binding_select(options=license_types, name='Select License Type:'),
    value=license_types[0]  # default value
)

# Base chart filtering the data based on the selected license type
base = alt.Chart(df).transform_filter(
    alt.datum['License Type'] == license_selector
)

# Bar mark to show monthly counts
bars = base.mark_bar().encode(
    x=alt.X('yearmonth(Original Issue Date):T', title='Month'),
    y=alt.Y('count()', title='Number of Licenses Issued'),
    tooltip=[alt.Tooltip('yearmonth(Original Issue Date):T', title='Month'),
             alt.Tooltip('count()', title='Count')]
)

# Line mark to show the trend over months, overlaid on bars
line = base.mark_line(point=True).encode(
    x=alt.X('yearmonth(Original Issue Date):T'),
    y=alt.Y('count()'),
    tooltip=[alt.Tooltip('yearmonth(Original Issue Date):T', title='Month'),
             alt.Tooltip('count()', title='Count')]
)

# Combine bars and line chart, then add interactive parameter
composite_chart = (bars + line).add_params(
    license_selector
).properties(
    title='Monthly License Issuance for Selected License Type',
    width=700,
    height=400
)
composite_chart

alt.LayerChart(...)